# **Ensemble learning VS Simple Moving Average**

# Introduction

We will build a model that more accurately predicts the unit sales for thousands of items sold at different Favorita stores.

[Link to the competition](https://www.kaggle.com/competitions/store-sales-time-series-forecasting)

[1st resource](https://www.kaggle.com/code/ekrembayar/store-sales-ts-forecasting-a-comprehensive-guide)

[2nd resource](https://www.kaggle.com/code/maricinnamon/store-sales-time-series-forecast-visualization#6.-Machine-learning-forecasting)

In [ ]:
import pandas as pd
import numpy as np
import plotly.express as px
import gc
import matplotlib.pyplot as plt
import statsmodels.api as sm

from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder
from statsmodels.tsa.deterministic import CalendarFourier, DeterministicProcess

# Models
from sklearn import linear_model
from sklearn.linear_model import ElasticNet, Lasso, Ridge
from xgboost import XGBRegressor
from sklearn.neighbors import KNeighborsRegressor
from sklearn.linear_model import LinearRegression

# Metrics
from sklearn.metrics import mean_squared_error
from sklearn.metrics import r2_score

Mounted at /content/drive/


In [ ]:
'''
from google.colab import drive

drive.mount("/content/drive/")

df_train = pd.read_csv(
    "/content/drive/MyDrive/Formations/Openclassrooms/Projet8/train.csv"
)
df_test = pd.read_csv(
    "/content/drive/MyDrive/Formations/Openclassrooms/Projet8/test.csv"
)

df_transac = pd.read_csv(
    "/content/drive/MyDrive/Formations/Openclassrooms/Projet8/transactions.csv"
)
df_stores = pd.read_csv(
    "/content/drive/MyDrive/Formations/Openclassrooms/Projet8/stores.csv"
)
df_holidays = pd.read_csv(
    "/content/drive/MyDrive/Formations/Openclassrooms/Projet8/holidays_events.csv"
)
df_oil = pd.read_csv("/content/drive/MyDrive/Formations/Openclassrooms/Projet8/oil.csv")

df_sample_sub = pd.read_csv(
    "/content/drive/MyDrive/Formations/Openclassrooms/Projet8/sample_submission.csv"
)
'''

# Import
df_train = pd.read_csv("../input/store-sales-time-series-forecasting/train.csv")
df_test = pd.read_csv("../input/store-sales-time-series-forecasting/test.csv")
df_stores = pd.read_csv("../input/store-sales-time-series-forecasting/stores.csv")
df_sample_sub = pd.read_csv("../input/store-sales-time-series-forecasting/sample_submission.csv")   
df_oil = pd.read_csv("../input/store-sales-time-series-forecasting/oil.csv")
df_holidays = pd.read_csv("../input/store-sales-time-series-forecasting/holidays.csv")
df_transac = pd.read_csv("../input/store-sales-time-series-forecasting/transactions.csv").sort_values(["store_nbr", "date"])

In [ ]:
df_all_data = pd.concat((df_train, df_test)).reset_index(drop=True)

In [ ]:
df_all_data = df_all_data.merge(df_transac, how="left")

In [ ]:
df_all_data = df_all_data.merge(df_stores)

We have multiple rows for one date in the 'holidays' dataframe. Hence, we can not use the data as it is now.

In [ ]:
df_holidays = df_holidays.groupby("date")["description"].apply(", ".join).reset_index()

In [ ]:
df_holidays.rename(columns={"type": "type_holidays"}, inplace=True)
df_all_data = df_all_data.merge(df_holidays, how="left", on="date")

#  Exploratory Data Analysis

## 1.1 Missing values

In [ ]:
df_all_data["date"] = pd.to_datetime(df_all_data.date)

In [ ]:
df_all_data.sort_values("date", inplace=True)

We only miss the sales data for the test data, which is good and makes sense.

In [ ]:
tmp_date = df_all_data["date"].unique()

In [ ]:
pd.date_range(start="2013-01-01", end="2017-08-31").difference(tmp_date)

DatetimeIndex(['2013-12-25', '2014-12-25', '2015-12-25', '2016-12-25'], dtype='datetime64[ns]', freq=None)

We just realized we do not have data for Christmas every year. Which also makes sense, because the stores must be closed.

In [ ]:
df_oil["date"] = pd.to_datetime(df_oil.date)
# Resample
df_oil = df_oil.set_index("date").dcoilwtico.resample("D").sum().reset_index()
# Interpolate
df_oil["dcoilwtico"] = np.where(df_oil["dcoilwtico"] == 0, np.nan, df_oil["dcoilwtico"])
df_oil.sort_values("dcoilwtico", inplace=True)
df_oil["dcoilwtico_interpolated"] = df_oil.dcoilwtico.interpolate()

We replace the NA values we have for the oil price using interpolation. The original methods leaves us with still one missing value in the original dataframe which was the first value. We will order the table in a different order to avoid this flaw of the interpolation function.

In [ ]:
df_all_data = df_all_data.merge(
    df_oil[["date", "dcoilwtico_interpolated"]], how="left", on="date"
)

Now we are clear with the oil price NA values.

## 1.2 Zero Forecasting

In [ ]:
df_zero_forecast = (
    df_all_data.groupby(["store_nbr", "family"])
    .sales.sum()
    .reset_index()
    .sort_values(["family", "store_nbr"])
)
df_zero_forecast = df_zero_forecast[df_zero_forecast.sales == 0]

In [ ]:
df_all_data.isna().sum()

id                               0
date                             0
store_nbr                        0
family                           0
sales                        28512
onpromotion                      0
transactions                274296
city                             0
state                            0
type                             0
cluster                          0
description                2578554
dcoilwtico_interpolated          0
dtype: int64

In [ ]:
print(df_all_data.shape)
# Anti Join
outer_join = df_all_data.merge(
    df_zero_forecast[df_zero_forecast.sales == 0].drop("sales", axis=1),
    how="outer",
    indicator=True,
)
df_all_data = outer_join[~(outer_join._merge == "both")].drop("_merge", axis=1)
del outer_join
gc.collect()

(3029400, 13)


0

In [ ]:
zero_prediction = []
for i in range(0, len(df_zero_forecast)):
    zero_prediction.append(
        pd.DataFrame(
            {
                "date": pd.date_range("2017-08-16", "2017-08-31").tolist(),
                "store_nbr": df_zero_forecast.store_nbr.iloc[i],
                "family": df_zero_forecast.family.iloc[i],
                "sales": 0,
            }
        )
    )
zero_prediction = pd.concat(zero_prediction)
del df_zero_forecast
gc.collect()

0

Some stores don't sell some product families. You can see which products aren't sold in which stores. It isn't difficult to forecast them next 15 days. Their forecasts must be 0 next 15 days. We can add them again at the end.

## 1.3 Plots

In [ ]:
graph1 = pd.merge(
    df_train.groupby(["date", "store_nbr"]).sales.sum().reset_index(),
    df_transac,
    how="left",
)
print(
    "Spearman Correlation between Total Sales and Transactions: {:,.4f}".format(
        graph1.corr("spearman").sales.loc["transactions"]
    )
)
px.line(
    df_transac.sort_values(["store_nbr", "date"]),
    x="date",
    y="transactions",
    color="store_nbr",
    title="Transactions",
)

Spearman Correlation between Total Sales and Transactions: 0.8175


There is a stable pattern in Transaction. All months are similar except December from 2013 to 2017 by boxplot. In addition, we've just seen same pattern for each store in previous plot. Store sales had always increased at the end of the year.

In [ ]:
df_transac["date"] = pd.to_datetime(df_transac.date)

df_transac_copy1 = df_transac.copy()
df_transac_copy1["year"] = df_transac_copy1.date.dt.year
df_transac_copy1["month"] = df_transac_copy1.date.dt.month
px.box(
    df_transac_copy1, x="year", y="transactions", color="month", title="Transactions"
)

df_transac_copy1 = (
    df_transac.set_index("date").resample("M").transactions.mean().reset_index()
)
df_transac_copy1["year"] = df_transac_copy1.date.dt.year
px.line(
    df_transac_copy1,
    x="date",
    y="transactions",
    color="year",
    title="Monthly Average Transactions",
)

We can see that transactions increase in spring and decrease after spring.

In [ ]:
px.scatter(
    graph1, x="transactions", y="sales", trendline="ols", trendline_color_override="red"
)

We can also see that there is a highly correlation between total sales and transactions.

In [ ]:
df_transac_copy1 = df_transac.copy()
df_transac_copy1["year"] = df_transac_copy1.date.dt.year
df_transac_copy1["dayofweek"] = df_transac_copy1.date.dt.dayofweek + 1
df_transac_copy1 = (
    df_transac_copy1.groupby(["year", "dayofweek"]).transactions.mean().reset_index()
)
px.line(
    df_transac_copy1,
    x="dayofweek",
    y="transactions",
    color="year",
    title="Transactions",
)

Last but not least, the day of the week is also very important. Every year, Saturday is the most important day of the week for shopping.

# Predictions

We will now make some predictions for the "sales" column between 2017-08-16 and 2017-08-31.

In [ ]:
df_train = df_all_data.loc[df_all_data["date"] < "2017-08-16"]
df_test = df_all_data.loc[df_all_data["date"] >= "2017-08-16"]

In [ ]:
X_train_original = df_train.drop("sales", axis=1)
X_test_original = df_test.drop("sales", axis=1)

y_train_original = df_train["sales"]
y_test_original = df_test["sales"]

## 3.1 Baseline model : Linear Regression

NB : we do not have transactions data for the test data so we will just drop it.

In [ ]:
X_train = X_train_original[:1].drop(
    ["date", "family", "city", "state", "type", "description", "transactions"], axis=1
)
X_test = X_test_original.drop(
    ["date", "family", "city", "state", "type", "description", "transactions"], axis=1
)

y_train = y_train_original[:1]
y_test = y_test_original

In [ ]:
X_test.isna().sum()

id                         0
store_nbr                  0
onpromotion                0
cluster                    0
dcoilwtico_interpolated    0
dtype: int64

In [ ]:
regr = linear_model.LinearRegression()
regr.fit(X_train, y_train)

LinearRegression()

In [ ]:
y_prediction = regr.predict(X_test)

In [ ]:
X_test["sales"] = y_prediction
X_test = X_test.merge(
    X_test_original[
        ["date", "family", "city", "state", "type", "description", "transactions"]
    ],
    left_index=True,
    right_index=True,
)

We just came up with our first prediction here. Let us compute some metrics to interprete how coherent this result is.

In [ ]:
y_train_lr = pd.DataFrame(df_train["date"])
y_train_lr["predictions"] = regr.predict(
    X_train_original.drop(
        ["date", "family", "city", "state", "type", "description", "transactions"],
        axis=1,
    )
)

In [ ]:
y_train_lr = y_train_lr.loc[
    (y_train_lr["date"] < "2016-08-20") & (y_train_lr["date"] >= "2016-08-02")
]

In [ ]:
df_train_tmp = df_train.loc[
    (df_train["date"] < "2016-08-20") & (df_train["date"] >= "2016-08-02")
]

In [ ]:
y_train_lr = y_train_lr["predictions"]

In [ ]:
from sklearn.metrics import mean_squared_log_error

print(
    "mean_squared_log_error is",
    np.sqrt(mean_squared_log_error(y_train_lr, df_train_tmp["sales"])),
)
# we want to check on our train data how well does the model fit the data

mean_squared_log_error is 4.323118610324769


Let us see if we can do better now.

## 3.2 Ensemble learning

In [ ]:
store_sales = df_all_data.copy()
store_sales.drop("transactions", axis=1, inplace=True)
store_sales["date"] = store_sales.date.dt.to_period("D")
store_sales = store_sales.set_index(["store_nbr", "family", "date"]).sort_index()

family_sales = (
    store_sales.groupby(["family", "date"]).mean().unstack("family").loc["2017"]
)

In [ ]:
# we'll add fit and predict methods to this minimal class
class BoostedHybrid:
    def __init__(self, model_1, model_2):
        self.model_1 = model_1
        self.model_2 = model_2
        self.y_columns = None  # store column names from fit method

In [ ]:
def fit(self, X_1, X_2, y):
    # train model_1
    self.model_1.fit(X_1, y)

    # make predictions
    y_fit = pd.DataFrame(
        self.model_1.predict(X_1),
        index=X_1.index,
        columns=y.columns,
    )

    # compute residuals
    y_resid = y - y_fit
    y_resid = y_resid.stack().squeeze()  # wide to long

    # train model_2 on residuals
    self.model_2.fit(X_2, y_resid)

    # save column names for predict method
    self.y_columns = y.columns
    # Save data for question checking
    self.y_fit = y_fit
    self.y_resid = y_resid


# Add method to class
BoostedHybrid.fit = fit

In [ ]:
def predict(self, X_1, X_2):
    # Predict with model_1
    y_pred = pd.DataFrame(
        self.model_1.predict(X_1),
        index=X_1.index,
        columns=self.y_columns,
    )
    y_pred = y_pred.stack().squeeze()  # wide to long

    # Add model_2 predictions to model_1 predictions
    y_pred += self.model_2.predict(X_2)

    return y_pred.unstack()


# Add method to class
BoostedHybrid.predict = predict

In [ ]:
# Target series
y = family_sales.loc[:, "sales"]


# X_1: Features for Linear Regression
dp = DeterministicProcess(index=y.index, order=1)
X_model_1 = dp.in_sample()


# X_2: Features for XGBoost
X_model_2 = family_sales.drop("sales", axis=1).stack()  # onpromotion feature

# Label encoding for 'family'
le = LabelEncoder()  # from sklearn.preprocessing
X_model_2 = X_model_2.reset_index("family")
X_model_2["family"] = le.fit_transform(X_model_2["family"])

# Label encoding for seasonality
X_model_2["day"] = X_model_2.index.day  # values are day of the month

In [ ]:
# Create model
model = BoostedHybrid(model_1=LinearRegression(), model_2=XGBRegressor())

In [ ]:
y_train, y_valid = y[:"2017-07-01"], y["2017-07-02":]
X_model_1_train, X_model_1_valid = X_model_1[:"2017-07-01"], X_model_1["2017-07-02":]
X_model_2_train, X_model_2_valid = (
    X_model_2.loc[:"2017-07-01"],
    X_model_2.loc["2017-07-02":],
)
X_model_2_train.fillna(0, inplace=True)

model.fit(X_model_1_train, X_model_2_train, y_train)
y_fit = model.predict(X_model_1_train, X_model_2_train).clip(0.0)
y_pred = model.predict(X_model_1_valid, X_model_2_valid).clip(0.0)

families = y.columns[0:6]
axs = y.loc(axis=1)[families].plot(
    subplots=True,
    sharex=True,
    figsize=(30, 20),
    color="0.75",
    style=".-",
    markeredgecolor="0.25",
    markerfacecolor="0.25",
    alpha=0.5,
)
_ = y_fit.loc(axis=1)[families].plot(subplots=True, sharex=True, color="C0", ax=axs)
_ = y_pred.loc(axis=1)[families].plot(subplots=True, sharex=True, color="C3", ax=axs)
for ax, family in zip(axs, families):
    ax.legend([])
    ax.set_ylabel(family)

/usr/local/lib/python3.8/dist-packages/pandas/core/frame.py:5176: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



[17:28:59] WARNING: /workspace/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.


/usr/local/lib/python3.8/dist-packages/pandas/plotting/_matplotlib/__init__.py:71: UserWarning:

When passing multiple axes, sharex and sharey are ignored. These settings must be specified when creating axes

/usr/local/lib/python3.8/dist-packages/pandas/plotting/_matplotlib/__init__.py:71: UserWarning:

When passing multiple axes, sharex and sharey are ignored. These settings must be specified when creating axes



In [ ]:
y_pred["date"] = y_pred.index

In [ ]:
y_pred_tmp = y_pred.melt(id_vars=["date"], var_name="Family", value_name="Value")

In [ ]:
y_pred = y_pred_tmp.loc[y_pred_tmp["date"] < "2017-08-16"]

In [ ]:
df_train_tmp = df_train.loc[
    (df_train["date"] < "2017-08-16") & (df_train["date"] >= "2017-07-02")
]

In [ ]:
df_train_tmp = df_train_tmp[["date", "family", "sales"]]

In [ ]:
df_train_ensemble_learning = df_train_tmp.groupby(
    by=["date", "family"], as_index=False
).sum()
df_train_ensemble_learning = df_train_ensemble_learning.sort_values(
    by=["family", "date"]
)

In [ ]:
print(
    "mean_squared_log_error is",
    np.sqrt(
        mean_squared_log_error(y_pred["Value"], df_train_ensemble_learning["sales"])
    ),
)

mean_squared_log_error is 4.668889831313944


The metric here is a bit higher than in the first model, which means our approach did not perform better. We can actually confirm this using the plots above: our model predicts seasonality for families where there is no seasonality at all, which causes the Mean Squared Log Error to rise a little.

## 3.3 Simple Moving Average

In [ ]:
df_all_data_sma = df_all_data.copy()
df_train_sma = df_train.copy()

In [ ]:
df_sales_sma = (
    df_all_data_sma[(df_all_data_sma.sales.notnull())]
    .groupby(["date", "family"])
    .sales.mean()
    .reset_index()
    .set_index("date")
)
"""
for num, i in enumerate(df_sales_sma.family.unique()):
    try:
        fig, ax = plt.subplots(1, 2, figsize=(15, 5))
        graph1 = df_sales_sma[(df_sales_sma.family == i)]  # & (a.sales.notnull())
        sm.graphics.tsa.plot_acf(
            graph1.sales, lags=365, ax=ax[0], title="AUTOCORRELATION\n" + i
        )
        sm.graphics.tsa.plot_pacf(
            graph1.sales, lags=365, ax=ax[1], title="PARTIAL AUTOCORRELATION\n" + i
        )
    except:
        pass
"""

'\nfor num, i in enumerate(df_sales_sma.family.unique()):\n    try:\n        fig, ax = plt.subplots(1, 2, figsize=(15, 5))\n        graph1 = df_sales_sma[(df_sales_sma.family == i)]  # & (a.sales.notnull())\n        sm.graphics.tsa.plot_acf(\n            graph1.sales, lags=365, ax=ax[0], title="AUTOCORRELATION\n" + i\n        )\n        sm.graphics.tsa.plot_pacf(\n            graph1.sales, lags=365, ax=ax[1], title="PARTIAL AUTOCORRELATION\n" + i\n        )\n    except:\n        pass\n'

We will try with lags 20, 30, 45, 365, 730 from PACF. 

In [ ]:
df_all_data_sorted = df_all_data.sort_values(["store_nbr", "family", "date"])

for i in [20, 30, 45, 60, 90, 120, 365, 730]:
    df_all_data_sorted["SMA" + str(i) + "_sales_lag16"] = (
        df_all_data_sorted.groupby(["store_nbr", "family"])
        .rolling(i)
        .sales.mean()
        .shift(16)
        .values
    )
    df_all_data_sorted["SMA" + str(i) + "_sales_lag30"] = (
        df_all_data_sorted.groupby(["store_nbr", "family"])
        .rolling(i)
        .sales.mean()
        .shift(30)
        .values
    )
    df_all_data_sorted["SMA" + str(i) + "_sales_lag60"] = (
        df_all_data_sorted.groupby(["store_nbr", "family"])
        .rolling(i)
        .sales.mean()
        .shift(60)
        .values
    )
print("Correlation")
df_all_data_sorted[
    ["sales"]
    + df_all_data_sorted.columns[
        df_all_data_sorted.columns.str.startswith("SMA")
    ].tolist()
].corr()

Correlation


sales  SMA20_sales_lag16  SMA20_sales_lag30  \
sales               1.000000           0.915878           0.900937   
SMA20_sales_lag16   0.915878           1.000000           0.985993   
SMA20_sales_lag30   0.900937           0.985993           1.000000   
SMA20_sales_lag60   0.881120           0.957782           0.968676   
SMA30_sales_lag16   0.915143           0.997381           0.994361   
SMA30_sales_lag30   0.902502           0.983344           0.997381   
SMA30_sales_lag60   0.878385           0.960818           0.969770   
SMA45_sales_lag16   0.916428           0.992844           0.996124   
SMA45_sales_lag30   0.904326           0.981125           0.992844   
SMA45_sales_lag60   0.878210           0.961741           0.971758   
SMA60_sales_lag16   0.917071           0.989465           0.993479   
SMA60_sales_lag30   0.903677           0.980519           0.989465   
SMA60_sales_lag60   0.877764           0.960886           0.971672   
SMA90_sales_lag16   0.915222           0.985392           0.989192   
SMA90_sales_lag30   0.901689           0.977067           0.985392   
SMA90_sales_lag60   0.874354           0.957767           0.968534   
SMA120_sales_lag16  0.912324           0.980745           0.985168   
SMA120_sales_lag30  0.898656           0.973323           0.980745   
SMA120_sales_lag60  0.872643           0.954856           0.965674   
SMA365_sales_lag16  0.910857           0.969702           0.971426   
SMA365_sales_lag30  0.899953           0.967173           0.969702   
SMA365_sales_lag60  0.875360           0.957375           0.965707   
SMA730_sales_lag16  0.913464           0.970431           0.970726   
SMA730_sales_lag30  0.898855           0.969025           0.970431   
SMA730_sales_lag60  0.868593           0.956697           0.967253   

                    SMA20_sales_lag60  SMA30_sales_lag16  SMA30_sales_lag30  \
sales                        0.881120           0.915143           0.902502   
SMA20_sales_lag16            0.957782           0.997381           0.983344   
SMA20_sales_lag30            0.968676           0.994361           0.997381   
SMA20_sales_lag60            1.000000           0.967812           0.976342   
SMA30_sales_lag16            0.967812           1.000000           0.991923   
SMA30_sales_lag30            0.976342           0.991923           1.000000   
SMA30_sales_lag60            0.997381           0.970174           0.976524   
SMA45_sales_lag16            0.976635           0.997391           0.997683   
SMA45_sales_lag30            0.988852           0.988678           0.997391   
SMA45_sales_lag60            0.992844           0.971707           0.977263   
SMA60_sales_lag16            0.986771           0.994174           0.996674   
SMA60_sales_lag30            0.992608           0.986956           0.994174   
SMA60_sales_lag60            0.989465           0.971177           0.977237   
SMA90_sales_lag16            0.989696           0.989992           0.992694   
SMA90_sales_lag30            0.989868           0.983239           0.989992   
SMA90_sales_lag60            0.985392           0.968301           0.974126   
SMA120_sales_lag16           0.988314           0.985610           0.989303   
SMA120_sales_lag30           0.987625           0.979194           0.985610   
SMA120_sales_lag60           0.980745           0.965493           0.971037   
SMA365_sales_lag16           0.973675           0.973694           0.975265   
SMA365_sales_lag30           0.972722           0.971314           0.973694   
SMA365_sales_lag60           0.969702           0.967771           0.969131   
SMA730_sales_lag16           0.971662           0.972807           0.973258   
SMA730_sales_lag30           0.971339           0.971615           0.972807   
SMA730_sales_lag60           0.970431           0.968241           0.969659   

                    SMA30_sales_lag60  SMA45_sales_lag16  SMA45_sales_lag30  \
sales                        0.878385           0.916428           0

In [ ]:
"""
df_all_data_lags = df_all_data_sorted[(df_all_data_sorted.store_nbr == 1)].set_index(
    "date"
)
"""
df_all_data_lags = df_all_data_sorted.set_index("date")

In [ ]:
def ewm_features(dataframe, alphas, lags):

    """Finds the best combination for our data in different alphas and lags"""

    dataframe = dataframe.copy()
    for alpha in alphas:
        for lag in lags:
            dataframe[
                "sales_ewm_alpha_" + str(alpha).replace(".", "") + "_lag_" + str(lag)
            ] = dataframe.groupby(["store_nbr", "family"])["sales"].transform(
                lambda x: x.shift(lag).ewm(alpha=alpha).mean()
            )
    return dataframe


alphas = [0.95, 0.9, 0.8, 0.7, 0.5]
lags = [16, 30, 60, 90]

df_all_data_sorted = ewm_features(df_all_data_sorted, alphas, lags)

In [ ]:
df_all_data_lags_copy = df_all_data_lags.copy()

In [ ]:
df_all_data_lags_copy["date2"] = df_all_data_lags_copy.index
df_all_data_lags_copy = df_all_data_lags_copy.loc[
    (df_all_data_lags_copy["date2"] < "2016-08-07")
    & (df_all_data_lags_copy["date2"] >= "2016-08-06")
]
df_train_tmp = df_train.loc[
    (df_train["date"] < "2016-08-07") & (df_train["date"] >= "2016-08-06")
]
df_train_grouped_sma = df_train_tmp.groupby(by=["date", "family"], as_index=False).sum()
"""
df_train_grouped_sma = df_train_grouped_sma.loc[
    df_train_grouped_sma["family"] != "BABY CARE"
]
"""
df_train_grouped_sma = df_train_grouped_sma.sort_values(by=["family", "date"])

In [ ]:
df_all_data_lags_copy = df_all_data_lags_copy.groupby(
    by=["date2", "family"], as_index=False
).sum()

In [ ]:
df_all_data_lags_copy.drop(
    columns=[
        "id",
        "store_nbr",
        "family",
        "sales",
        "onpromotion",
        "transactions",
        "cluster",
        "dcoilwtico_interpolated",
        "date2",
    ],
    axis=1,
    inplace=True,
)

In [ ]:
def pick_best_rmsle(df1, df2):

    """Takes in two dataframes, looks for the best RMSLE value between df1 and a column specified in df2 then returns this column"""

    metrics_list = []

    for i in df_all_data_lags_copy.columns:
        metrics_list.append(
            np.sqrt(mean_squared_log_error(df2["sales"], df_all_data_lags_copy[i]))
        )

    min_value = min(metrics_list)
    index_min_lag = metrics_list.index(min_value)
    best_lag = df_all_data_lags_copy.columns[index_min_lag]

    return best_lag

In [ ]:
pick_best_rmsle(df_all_data_lags_copy, df_train_grouped_sma)

'SMA120_sales_lag16'

In [ ]:
df_all_data_lags["date2"] = df_all_data_lags.index

df_all_data_lags_output = df_all_data_lags.loc[
    (
        df_all_data_lags["date2"] >= "2017-08-15"
    )  # & (df_all_data_lags["date2"] >= "2017-08-01")
]

In [ ]:
df_output = df_all_data_lags_output[
    ["id", "family", "SMA120_sales_lag16"]
].reset_index()
df_output[:28512].sort_values("id", inplace=True)

/usr/local/lib/python3.8/dist-packages/pandas/util/_decorators.py:311: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [ ]:
df_sub_final = df_sample_sub
df_sub_final["sales"] = df_output[["SMA120_sales_lag16"]]
# df_sub_final.columns = ['id', 'sales']

In [ ]:
df_sub_final.to_csv("submission_kernel_P8.csv", index=False)